In [2]:
%reload_ext tensorboard
# Clear any logs from previous runs
!rm -rf ./logs/

In [3]:
import tensorflow as tf
from tensorboard.plugins.hparams import api as hp
import numpy as np
from sklearn.preprocessing import StandardScaler
import pandas as pd
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input,Conv2D,MaxPooling2D,UpSampling2D, Dense
from sklearn.preprocessing import StandardScaler, MinMaxScaler


In [4]:
file = 'data/jla_lcparams.txt'
data = pd.read_csv(file, sep = " " ,usecols=['zcmb', 'mb', 'dmb'] )
data.head()
# plt.show()

# syscov = np.loadtxt('data/pantheon_errors.txt',skiprows=1).reshape((1048,1048))

# dataFull = np.concatenate([data.values, syscov], axis=1)

x = data.values[:, 0]
Y = data.values[:, 1:]

# print(np.shape(dataFull))
# randomize = np.random.permutation(len(data.values))
shuffle = [x for x in range(len(data.values)) if x%2==1]
odd = [x for x in range(len(data.values)) if x%2==0]
shuffle.extend(odd)

X = x[shuffle]
y = Y[shuffle]
print(shuffle)

scalerx = StandardScaler()
scalerx.fit(X.reshape(-1,1))
X = scalerx.transform(X.reshape(-1,1))

# scalery = StandardScaler()
# scalery.fit(Y)
# y = scalery.transform(y)

split = 0.8
ntrain = int(split * len(X))
indx = [ntrain]
X_train, X_test = np.split(X, indx)
y_train, y_test = np.split(y, indx)

[1, 3, 5, 7, 9, 11, 13, 15, 17, 19, 21, 23, 25, 27, 29, 31, 33, 35, 37, 39, 41, 43, 45, 47, 49, 51, 53, 55, 57, 59, 61, 63, 65, 67, 69, 71, 73, 75, 77, 79, 81, 83, 85, 87, 89, 91, 93, 95, 97, 99, 101, 103, 105, 107, 109, 111, 113, 115, 117, 119, 121, 123, 125, 127, 129, 131, 133, 135, 137, 139, 141, 143, 145, 147, 149, 151, 153, 155, 157, 159, 161, 163, 165, 167, 169, 171, 173, 175, 177, 179, 181, 183, 185, 187, 189, 191, 193, 195, 197, 199, 201, 203, 205, 207, 209, 211, 213, 215, 217, 219, 221, 223, 225, 227, 229, 231, 233, 235, 237, 239, 241, 243, 245, 247, 249, 251, 253, 255, 257, 259, 261, 263, 265, 267, 269, 271, 273, 275, 277, 279, 281, 283, 285, 287, 289, 291, 293, 295, 297, 299, 301, 303, 305, 307, 309, 311, 313, 315, 317, 319, 321, 323, 325, 327, 329, 331, 333, 335, 337, 339, 341, 343, 345, 347, 349, 351, 353, 355, 357, 359, 361, 363, 365, 367, 369, 371, 373, 375, 377, 379, 381, 383, 385, 387, 389, 391, 393, 395, 397, 399, 401, 403, 405, 407, 409, 411, 413, 415, 417, 419, 421,

In [5]:
callbacks = [tf.keras.callbacks.EarlyStopping(monitor='val_loss', mode='min',
                                   min_delta=0,
                                   patience=10,
                                   restore_best_weights=True)]



In [6]:
HP_NUM_UNITS1 = hp.HParam('num_units1', hp.Discrete([100, 200, 300, 400, 500]))
HP_NUM_UNITS2 = hp.HParam('num_units2', hp.Discrete([100, 200,300, 400, 500]))
HP_NUM_UNITS3 = hp.HParam('num_units3', hp.Discrete([100, 200,300, 400, 500]))
# HP_DROPOUT = hp.HParam('dropout', hp.RealInterval(0.0, 0.2))
# HP_OPTIMIZER = hp.HParam('optimizer', hp.Discrete(['adam', 'sgd']))
# HP_OPTIMIZER = hp.HParam('optimizer', hp.Discrete(['adam', 'Adadelta']))
# HP_OPTIMIZER = hp.HParam('optimizer', hp.Discrete(['adam']))
HP_BATCHSIZE = hp.HParam('batch_size', hp.Discrete([16, 32,64]))

In [7]:
# sess = tf.Session()
# writer = tf.summary.FileWriter("/tmp/tfvgg", sess.graph)
# init = tf.initialize_all_variables()
# sess.run(init)
# with tf.summary.create_file_writer('logs/hparam_tuning').as_default():
#     hp.hparams_config(
#         hparams=[HP_NUM_UNITS1, HP_NUM_UNITS2, HP_NUM_UNITS3, HP_NUM_UNITS4,
#                  HP_OPTIMIZER, HP_BATCHSIZE],
#         metrics=[hp.Metric('loss', display_name="Loss")])

In [8]:
# METRIC_ACCURACY = 'accuracy'
with tf.summary.create_file_writer('logs/hparam_tuning').as_default():
# with tf.summary.FileWriter('logs/hparam_tuning', sess.graph):
#     init = tf.initialize_all_variables()
#     sess.run(init)
    hp.hparams_config(
        hparams=[HP_NUM_UNITS1, HP_NUM_UNITS2, HP_NUM_UNITS3, HP_BATCHSIZE],
        metrics=[hp.Metric('loss', display_name="Loss")])

In [9]:
# def annmodel(input_z, hparams):
#     efirst = Dense(hparams[HP_NUM_UNITS1], activation='relu', input_shape=(1,))(input_z)
#     tf.keras.layers.Dropout(hparams[HP_DROPOUT]),
#     ehidden2 = Dense(hparams[HP_NUM_UNITS2], activation='relu')(efirst)
#     ehidden3 = Dense(hparams[HP_NUM_UNITS3], activation='relu')(ehidden2)    
#     elast = Dense(2, activation='relu')(ehidden3)
       
#     return elast

In [10]:
epochs = 300
# input_z = Input(shape = (1,))


In [11]:
def train_test_model(hparams):
    model = tf.keras.models.Sequential([
#         tf.keras.layers.Flatten(),
        tf.keras.layers.Dense(hparams[HP_NUM_UNITS1], activation=tf.nn.relu, input_shape=(1,)),
#         tf.keras.layers.Dropout(hparams[HP_DROPOUT]),
        tf.keras.layers.Dense(hparams[HP_NUM_UNITS2], activation=tf.nn.relu),
#         tf.keras.layers.Dropout(hparams[HP_DROPOUT]),
        tf.keras.layers.Dense(hparams[HP_NUM_UNITS3], activation=tf.nn.relu),
#         tf.keras.layers.Dropout(hparams[HP_DROPOUT]),
        tf.keras.layers.Dense(2)
    ])
                              
    model.compile(
#             optimizer=hparams[HP_OPTIMIZER],
            optimizer='adam',
            loss='mean_squared_error',
            metrics=['mean_squared_error']
          )
    # Run with 1 epoch to speed things up for demo purposes
    # model.fit(x_train, y_train, epochs=1, callbacks=callbacks) 
    # _, loss = model.evaluate(x_test, y_test)
    model.fit(X_train, y_train, epochs=epochs, 
              batch_size=hparams[HP_BATCHSIZE], callbacks=callbacks, verbose=0) 
    _, loss = model.evaluate(X_test, y_test)


    return loss
    

In [12]:
def run(run_dir, hparams):
    with tf.summary.create_file_writer(run_dir).as_default():
#     with tf.summary.FileWriter(run_dir):
        hp.hparams(hparams)  # record the values used in this trial
        loss = train_test_model(hparams)
        tf.summary.scalar("loss", loss, step=1)

In [ ]:
session_num = 0

for batch_size in HP_BATCHSIZE.domain.values:
    for num_units1 in HP_NUM_UNITS1.domain.values:
        for num_units2 in HP_NUM_UNITS2.domain.values:
            for num_units3 in HP_NUM_UNITS3.domain.values:
#                 for dropout_rate in (HP_DROPOUT.domain.min_value, HP_DROPOUT.domain.max_value):
#       for dropout_rate in (HP_DROPOUT.domain.min_value, HP_DROPOUT.domain.max_value):
#                     for optimizer in HP_OPTIMIZER.domain.values:
                hparams = {
                  HP_NUM_UNITS1: num_units1,
                  HP_NUM_UNITS2: num_units2,
                  HP_NUM_UNITS3: num_units3,
#                       HP_NUM_UNITS4: num_units4,
#                   HP_DROPOUT: dropout_rate,
#                       HP_OPTIMIZER: optimizer,
                  HP_BATCHSIZE: batch_size
                }
                run_name = "run-%d" % session_num
                print('--- Starting trial: %s' % run_name)
                print({h.name: hparams[h] for h in hparams})
                run('logs/hparam_tuning/' + run_name, hparams)
                session_num += 1

print(session_num)

--- Starting trial: run-0
{'num_units1': 100, 'num_units2': 100, 'num_units3': 100, 'batch_size': 16}


5/5 [==============================] - 0s 816us/step - loss: 0.0677 - mean_squared_error: 0.0677
--- Starting trial: run-1
{'num_units1': 100, 'num_units2': 100, 'num_units3': 200, 'batch_size': 16}


5/5 [==============================] - 0s 872us/step - loss: 0.0524 - mean_squared_error: 0.0524
--- Starting trial: run-2
{'num_units1': 100, 'num_units2': 100, 'num_units3': 300, 'batch_size': 16}


5/5 [==============================] - 0s 751us/step - loss: 0.0695 - mean_squared_error: 0.0695
--- Starting trial: run-3
{'num_units1': 100, 'num_units2': 100, 'num_units3': 400, 'batch_size': 16}


5/5 [==============================] - 0s 704us/step - loss: 0.0533 - mean_squared_error: 0.0533
--- Starting trial: run-4
{'num_units1': 100, 'num_units2': 100, 'num_units3': 500, 'batch_size': 16}


...

5/5 [==============================] - 0s 2ms/step - loss: 0.0801 - mean_squared_error: 0.0801
--- Starting trial: run-183
{'num_units1': 300, 'num_units2': 200, 'num_units3': 400, 'batch_size': 32}


5/5 [==============================] - 0s 2ms/step - loss: 0.0572 - mean_squared_error: 0.0572
--- Starting trial: run-184
{'num_units1': 300, 'num_units2': 200, 'num_units3': 500, 'batch_size': 32}


5/5 [==============================] - 0s 2ms/step - loss: 0.0572 - mean_squared_error: 0.0572
--- Starting trial: run-185
{'num_units1': 300, 'num_units2': 300, 'num_units3': 100, 'batch_size': 32}


5/5 [==============================] - 0s 1ms/step - loss: 0.0639 - mean_squared_error: 0.0639
--- Starting trial: run-186
{'num_units1': 300, 'num_units2': 300, 'num_units3': 200, 'batch_size': 32}


5/5 [==============================] - 0s 1ms/step - loss: 0.0588 - mean_squared_error: 0.0588
--- Starting trial: run-187
{'num_units1': 300, 'num_units2': 300, 'num_units3': 300, 'batch_size': 32}


In [ ]:
%tensorboard --logdir logs/hparam_tuning